<h1><center>Laboratorio 7: Interpretabilidad 🤖</center></h1>

<center><strong>MDS7202: Laboratorio de Programación Científica para Ciencia de Datos - Primavera 2025</strong></center>

### Cuerpo Docente:

- Profesores: Diego Cortez, Gabriel Iturra
- Auxiliares: Melanie Peña, Valentina Rojas
- Ayudantes: Nicolás Cabello, Cristopher Urbina

### Equipo: SUPER IMPORTANTE - notebooks sin nombre no serán revisados

- Nombre de alumno 1: Andres Oñate
- Nombre de alumno 2: Javier Zapata


### **Link de repositorio de GitHub:** [Insertar Repositorio](https://github.com/andresignacio-o/MDS7202)

### Indice

1. [Temas a tratar](#Temas-a-tratar:)
3. [Descripcción del laboratorio](#Descripción-del-laboratorio.)
4. [Desarrollo](#Desarrollo)

## Temas a tratar

- Clasificación usando `XGBoost`.
- Métodos Agnósticos Globales de Interpretabilidad (`Partial Dependence Plot`, `Permutation Feature Importance`)
- Métodos Agnósticos Locales de Interpretabilidad (`Scoped Rules`, `SHAP`)

## Reglas:

- **Grupos de 2 personas**
- Fecha de entrega: Entregas Martes a las 23:59.
- Instrucciones del lab el viernes a las 16:15 en formato online. Asistencia no es obligatoria, pero se recomienda **fuertemente** asistir.
- <u>Prohibidas las copias</u>. Cualquier intento de copia será debidamente penalizado con el reglamento de la escuela.
- Tienen que subir el laboratorio a u-cursos y a su repositorio de github. Labs que no estén en u-cursos no serán revisados. Recuerden que el repositorio también tiene nota.
- Cualquier duda fuera del horario de clases al foro. Mensajes al equipo docente serán respondidos por este medio.
- Pueden usar cualquier material del curso que estimen conveniente.


### Objetivos principales del laboratorio

- Generar un pipeline de clasificación con `XGBoost`.
- Implementar modelos de interpretabilidad para explicar el funcionamiento del modelo de clasificación.

El laboratorio deberá ser desarrollado sin el uso indiscriminado de iteradores nativos de python (aka "for", "while"). La idea es que aprendan a exprimir al máximo las funciones optimizadas que nos entrega `pandas`, las cuales vale mencionar, son bastante más eficientes que los iteradores nativos sobre DataFrames.

# 1. Problemas Clínicos del Dr. Simi

<p align="center">
  <img src="https://gantz.cl/wp-content/uploads/2020/01/79024136_2718114448239059_7240913062570491904_o.jpg" width="350">
</p>

El reconocido **Dr. Simi**, famoso vendedor de medicamentos en latinoamerica, debido a la creciente prevalencia de enfermedades crónicas, como la diabetes, decidió abrir una clínica especializada en el tratamiento de esta enfermedad en nuestro país.

La clínica del Doctor Simi se convirtió en un lugar donde los pacientes con diabetes podrían recibir atención médica integral. El personal médico estaba compuesto por especialistas en endocrinología, nutrición y enfermería, todos capacitados en el manejo de la diabetes.

Sin embargo él se ha dado cuenta que los tiempos han cambiado y gracias a las tecnologías es posible generar mejores predicciones en la diabetes conociendo el historial médico de las personas. Por esto, el doctor se ha colocado una meta de incluir modelos de machine learning dentro de sus clínicas, para ello le ha solicitado crear un modelo capaz de predecir/clasificar diabetes pero le rogó que el desarrollo del modelo tuviera un especial enfoque en la interpretabilidad de lo que hace su modelo.

Para que usted pueda entrenar el modelo, Dr. Simi le ha entregado un dataset de todos los clientes que fueron detectados con diabetes a lo largo de la historia de la clinica. Con ello, adjunta el historial médico de las personas en forma de datos tabulares para que usted pueda realizar fácilmente la clasificación.


In [1]:
import numpy as np
import pandas as pd

df = pd.read_csv('diabetes_data.csv')
df.head(5)

Age  Sex  HighChol  CholCheck   BMI  Smoker  HeartDiseaseorAttack  \
0   4.0  1.0       0.0        1.0  26.0     0.0                   0.0   
1  12.0  1.0       1.0        1.0  26.0     1.0                   0.0   
2  13.0  1.0       0.0        1.0  26.0     0.0                   0.0   
3  11.0  1.0       1.0        1.0  28.0     1.0                   0.0   
4   8.0  0.0       0.0        1.0  29.0     1.0                   0.0   

   PhysActivity  Fruits  Veggies  HvyAlcoholConsump  GenHlth  MentHlth  \
0           1.0     0.0      1.0                0.0      3.0       5.0   
1           0.0     1.0      0.0                0.0      3.0       0.0   
2           1.0     1.0      1.0                0.0      1.0       0.0   
3           1.0     1.0      1.0                0.0      3.0       0.0   
4           1.0     1.0      1.0                0.0      2.0       0.0   

   PhysHlth  DiffWalk  Stroke  HighBP  Diabetes  
0      30.0       0.0     0.0     1.0       0.0  
1       0.0       0.0     1.0     1.0       0.0  
2      10.0       0.0     0.0     0.0       0.0  
3       3.0       0.0     0.0     1.0       0.0  
4       0.0       0.0     0.0     0.0       0.0

## 2. Clasificación de pacientes con diabetes (5 puntos)

<p align="center">
  <img src="https://media.tenor.com/QH--g3ZaSbsAAAAC/dr-simi-abrazo.gif" width="400">
</p>

Tareas:
1. En primer lugar, el reconocido doctor le pide entrenar un modelo de `XGBoost` utilizando como target la columna `Diabetes` del dataset `diabetes_data.csv`. Para el entrenamiento, realice los siguientes pasos:
  * Realice una breve exploración de los datos y determine si aplicará transformaciones (MinMaxScaler, StandardScaler, etc.) en alguna/s de las variables. (1 punto)
  * Cree un conjunto de entrenamiento y uno de prueba, con una proporción de 1/3 en el conjunto de prueba. (0.5 puntos)
  * Cree un ColumnTransformer de preprocesamiento donde aplique las transformaciones determinadas anteriormente. Fije el parámetro `verbose_feature_names_out=False` y fije la salida del ColumnTransformer en formato pandas mediante el método `.set_output(transform='pandas')`. (1 punto)
  *  Cree un pipeline donde integre el preprocesamiento y el modelo `XGBoost` y entrene el modelo. Luego utilice `classification_report(..)` para reportar el desempeño del modelo. (1 punto)

Comente sus decisiones y los resultados obtenidos con el modelo.

2. Luego, le pide responder las siguientes preguntas:
  *  ¿Es acaso un buen predictor de diabetes? (0.5 puntos)
  * ¿Qué buscan explicar las métricas utilizadas? (0.5 puntos)
  * ¿Las métricas utilizadas para medir la predictibilidad le permiten asegurar que su modelo haga una buena elección de las features?(0.5 puntos)

In [2]:
#!pip install xgboost

In [3]:
print(df.isnull().sum())


print(df.isnull().sum().sort_values(ascending=False))

Age                     0
Sex                     0
HighChol                0
CholCheck               0
BMI                     0
Smoker                  0
HeartDiseaseorAttack    0
PhysActivity            0
Fruits                  0
Veggies                 0
HvyAlcoholConsump       0
GenHlth                 0
MentHlth                0
PhysHlth                0
DiffWalk                0
Stroke                  0
HighBP                  0
Diabetes                0
dtype: int64
Age                     0
Sex                     0
HighBP                  0
Stroke                  0
DiffWalk                0
PhysHlth                0
MentHlth                0
GenHlth                 0
HvyAlcoholConsump       0
Veggies                 0
Fruits                  0
PhysActivity            0
HeartDiseaseorAttack    0
Smoker                  0
BMI                     0
CholCheck               0
HighChol                0
Diabetes                0
dtype: int64


In [4]:

binary_cols = []
numeric_cols = []

for col in df.columns:
    unique_vals = df[col].dropna().unique()
    
    if len(unique_vals) == 2 and np.all(np.isin(unique_vals, [0, 1])):  # estrictamente 0 y 1
        binary_cols.append(col)
    elif len(unique_vals) == 2:
        # Si son solo 2 valores pero no 0/1 (ej: 1/2 o -1/1)
        binary_cols.append(col)
    else:
        numeric_cols.append(col)

print(" Columnas binarias:")
print(binary_cols)
print("\n Columnas numéricas continuas/discretas:")
print(numeric_cols)

 Columnas binarias:
['Sex', 'HighChol', 'CholCheck', 'Smoker', 'HeartDiseaseorAttack', 'PhysActivity', 'Fruits', 'Veggies', 'HvyAlcoholConsump', 'DiffWalk', 'Stroke', 'HighBP', 'Diabetes']

 Columnas numéricas continuas/discretas:
['Age', 'BMI', 'GenHlth', 'MentHlth', 'PhysHlth']


In [5]:
import plotly.express as px

for col in numeric_cols:
    fig = px.histogram(
        df,
        x=col,
        nbins=30,
        title=f"Histograma de {col}",
        labels={col: col, "count": "Frecuencia"},
        opacity=0.75
    )
    fig.update_layout(
        bargap=0.1,
        title_x=0.5,
        template="plotly_white"
    )
    fig.show()


In [6]:
from sklearn.model_selection import train_test_split

X = df.drop(columns=['Diabetes'])
y = df['Diabetes']

X_train, X_test, y_train, y_test = train_test_split(
    X, y, test_size=1/3, random_state=42, stratify=y
)


In [7]:

outlier_cols = ['MentHlth', 'PhysHlth']

standard_cols = [c for c in numeric_cols if c not in outlier_cols]

binary_cols = [col for col in binary_cols if col != 'Diabetes']

In [8]:
from sklearn.compose import ColumnTransformer
from sklearn.preprocessing import StandardScaler, RobustScaler

preprocessor = ColumnTransformer(
    transformers=[
        ("standard", StandardScaler(), standard_cols),
        ("robust", RobustScaler(), outlier_cols),
        ("binary", "passthrough", binary_cols)
    ],
    verbose_feature_names_out=False
).set_output(transform="pandas")


In [9]:
for col_list in [standard_cols, outlier_cols, binary_cols]:
    for col in col_list:
        if col not in X_train.columns:
            print(f"Columna no encontrada: {col}")


In [10]:
from sklearn.pipeline import Pipeline
from xgboost import XGBClassifier
from sklearn.metrics import classification_report

# Definir el modelo
xgb = XGBClassifier(
    n_estimators=200,
    learning_rate=0.1,
    max_depth=4,
    random_state=42,
    eval_metric='logloss'
)

# Crear pipeline
pipe = Pipeline([
    ("preprocessor", preprocessor),
    ("model", xgb)
])

# Entrenar
pipe.fit(X_train, y_train)

# Predicciones
y_pred = pipe.predict(X_test)

# Reporte
print(classification_report(y_test, y_pred))


              precision    recall  f1-score   support

         0.0       0.78      0.71      0.74     11782
         1.0       0.73      0.80      0.76     11782

    accuracy                           0.75     23564
   macro avg       0.75      0.75      0.75     23564
weighted avg       0.75      0.75      0.75     23564



Se utilizo un escalado estandar para las variables que presentaban una distribución parecida a una normal y un escalador mas robusto para las que parecian presentar outliers.

Debido a que este es un caso clinico y que la diabetes es una enfermedad considerada grave, se puede asumir que la mejor metrica para evaluar el modelo es recall sobre la clase 1, podemos ver que en este caso es de un 0.74, se considera aceptable un recall igual o superior a 0.75 (no sabemos si es un estandar, pero a veces requieren que los modelos tengan un rendimiento igual o mayor a 0.75) por lo que el modelo es insuficiente aunque por poco.

Nos basamos en Recall ya que entre más alta sea la cifra menos personas con cancer dejamos sin tratamiento. (Maximizar recall es minimizar falsos negativos)

Finalmente no se puede asegurar que solo con la métrica de interes adecuada el modelo eliga bien las features, tambien hay componentes de lógica asociados (es posible que una componente tenga alta correlacion pero sea irrelevante o engañoso)

## 3. Importancia de las features con XGBoost (5 puntos)

<p align="center">
  <img src="https://media.tenor.com/5JAj5_IiagEAAAAd/dr-simi-dr-simi-dance.gif" width="400">
</p>

Tareas:
1. Para añadir el toque de interpretabilidad que Dr. Simi le pide, se le pide calcular la **importancia de las features** del modelo entrenado utilizando todos los métodos (*weight*, *cover*, *gain*) que posee xgboost usando `plot_importance`. `Hint:` Puede acceder a un paso de un pipeline por su nombre mediante el método `.named_steps[...]` (3 puntos)
2. ¿Los resultados obtenidos con los diferentes métodos son compatibles?, comente sus resultados y a que se debe la igualdad o desigualdad que ve en los resultados. (1 punto)
3. Finalmente, ¿las importancias obtenidas son suficientes para obtener la interpretabilidad de un modelo que utiliza árboles? ¿Qué debilidad presenta este método? (1 punto)

In [11]:

# Acceder al modelo XGBoost entrenado dentro del pipeline
xgb_model = pipe.named_steps["model"]

# Tipos de importancia que queremos visualizar
importance_types = ["weight", "cover", "gain"]

# Extraer nombres de features desde el ColumnTransformer (opcional, si tienes pipeline)
feature_names = pipe.named_steps["preprocessor"].get_feature_names_out()

for imp_type in importance_types:
    # Obtener diccionario de importancia
    importance_dict = xgb_model.get_booster().get_score(importance_type=imp_type)
    
    # Convertir a DataFrame
    df_imp = pd.DataFrame({
        "feature": [feature_names[int(k[1:])] if k.startswith("f") else k for k in importance_dict.keys()],
        "importance": list(importance_dict.values())
    }).sort_values(by="importance", ascending=False)
    
    # Graficar con Plotly
    fig = px.bar(df_imp, x="importance", y="feature", orientation="h",
                 title=f"Importancia de Features por {imp_type}")
    fig.show()


En efecto los resultados difieren bastante de un metodo a otro, esto es normal dado que sirven para medir cosas distintas:
* Weight: cuenta cuántas veces una feature se utiliza para dividir los nodos en todos los árboles
* Gain: mide la mejora promedio en la función objetivo que aporta cada feature al hacer una división
* Cover: evalúa el número de muestras afectadas por una división que utiliza esa feature

La importancia por metodo da una buena idea de como se comportan la variable dependiente en base a las features, pero no son suficientes como para poder asegurar una interpretabilidad completa, por ejemplo, no es capaz de captar relaciones entre variables, además esta la elección de que método usar ya que como se vío, esto cambia la importancia de las features.

## 4. Métodos Agnósticos Globales (10 puntos)

<p align="center">
  <img src="https://media.tenor.com/JcRHtjVuXN8AAAAC/dr-simi-farmacias-similares.gif" width="400">
</p>

Tareas:
1. Para mitigar los problemas encontrados en la sección anterior, Dr. Simi le pide implementar un **método de permutación** que le permita observar la importancia de las features. `Nota:`Tenga cuidado con el orden de las columnas de este método. `Hint:` Puede obtener los features del clasificador con su respectivo orden mediante el método `.get_booster().feature_names` (2 puntos)
2. Para que su modelo sea consistente, repita el proceso **30 veces** y verifique la desviación estándar de sus resultados (¿Qué señala esta?). (2 puntos)
3. Visualice los resultados de este método en un gráfico. (2 puntos)
4. Además, responda las siguientes preguntas:
  - ¿Cómo mide la importancia de las features su propuesta? (1 punto)
  - ¿Qué features tienen un mayor impacto en la salida del modelo?. Comente las 5 primeras, ¿tienen sentido? (1 punto)
  - ¿Cómo cambian sus conclusiones con respecto a las features importances del punto anterior? (1 punto)
  - Nombre y explique 3 ventajas y 3 desventajas del método implementado. (1 punto)

In [12]:
from sklearn.inspection import permutation_importance
# Obtener el modelo XGBoost desde el pipeline
xgb_model = pipe.named_steps['model'] 

# Obtener nombres de las features en el mismo orden que el modelo
feature_names = xgb_model.get_booster().feature_names

features = X_test.columns
importances_df = pd.DataFrame(columns=features)

for i in range(30):
    result = permutation_importance(
        pipe, X_test, y_test,
        n_repeats=1,
        random_state=i,
        scoring='recall'
    )
    importances_df.loc[i] = result.importances_mean

mean_importances = importances_df.mean()
std_importances = importances_df.std()

# Calcular media y desviación estándar
mean_importances = importances_df.mean()
std_importances = importances_df.std()

# Crear DataFrame para visualización
viz_df = pd.DataFrame({
    'feature': mean_importances.index,
    'mean_importance': mean_importances.values,
    'std_importance': std_importances.values
}).sort_values(by='mean_importance', ascending=False)

# Visualización con px
fig = px.bar(
    viz_df,
    x='feature',
    y='mean_importance',
    error_y='std_importance',
    title='Importancia de Features por Permutación (30 repeticiones)',
    labels={'mean_importance': 'Importancia media', 'feature': 'Feature'}
)
fig.show()

Podemos observar por los "corchetes" en cada columna la desviación estandar para cada feature, es decir cuanto se desvia del promedio en las 30 repeticiones, entre menor sea esta mas consistentes los resultados.

El modelo se entrena en base a distintas features, y si una de ellas se permuta con otra y el rendimiento del modelo baja, entonces esa feature se considera mas importante que la otra.

Las features con mayor importancia son GenHlth, Age, BMI, con resultados bastante altos, seguidos de HighBP, HighChol que a pesar de ser de los 5 más relevantes, hay bastante diferencia entre estos 2 últimos y los primeros 3, el resultado es concordante con lo que uno esperaría ya que el BMI  y la edad con variables altamente asociadas a la diabetes, aunque bajan en importancia el colesterol y la presion sanguinea tambien estan correlacionadas con la diabetes, aunque es posible que estos efectos sean ya caprtados por las primeras 3 features.

Se pueden notar diferencias entre estos resultados y los obtenidos en la parte anterior, aunque GenHlth siempre se mantiene en el top 5 (y las otras se mantienen en el top 10), además en esta ultima forma calculando con permutación se puede ver que tanto afecta una variable probando diferentes features, entre más repeticiones se hagan mas fidedigno es el resultado con lo que se esperaría del verdadero rendimiento del modelo.

Las ventajas son:
* Es un metodo mas robusto dado que se basa en iteraciones con diferentes datos (divididos por features)
* Ayuda a la interpretación que se obtenga tambien la desviación estandar, con esto uno puede interpretar que tan estable son estos resultados
* Al evaluar sobre features distintas, puede captar efectos de relación entre variables de mejor manera

Las desventajas:
* Si se quiere llegar a mejores resultados hay que aumentar las iteraciones, lo cual entre más pesado el modelo mas pesado es

* Es menos directo ya que hay que elegir sobre que métrica ajustar

* Sigue pudiendo subestimar o sobreestimar una feature por su correlacion frente a otra feature (o a efectos no observables en el dataset pero correlacionados entre features)

## 5. Métodos Agnósticos Locales (20 puntos)

<p align="center">
  <img src="https://i.makeagif.com/media/10-24-2024/oMCrLI.gif" width="400">
</p>

### 5.1 Calculando Shap Values (4 puntos)

Tareas:
1. Alegre por saber cómo funciona el modelo de predicción a nivel general, Dr. Simi le pide ahora interpretar las predicciones de su modelo a nivel de paciente (es decir, desde un punto de vista **local**). Para esto, el ilustre farmacéutico le pide calcular los *shap values* de su modelo. (2 puntos)
2. ¿Qué representa cada número en su resultado? (1 punto)
3. ¿Es posible atribuir un significado a la positividad/negatividad de cada valor? (1 punto)

In [13]:
#!pip install shap

In [14]:
import warnings
warnings.filterwarnings("ignore", message=".*The 'nopython' keyword.*")

In [15]:
import shap
# Se extrae el modelo XGBoost entrenado desde el pipeline
xgb_model = pipe.named_steps["model"]

# Se transforma el conjunto de test para obtener las features procesadas
X_test_transformed = pipe.named_steps["preprocessor"].transform(X_test)
X_test_transformed = pd.DataFrame(
    X_test_transformed, 
    columns=pipe.named_steps["preprocessor"].get_feature_names_out()
)

# Se inicializa el explainer de SHAP
explainer = shap.TreeExplainer(xgb_model)

# Se calculan los valores SHAP
shap_values = explainer.shap_values(X_test_transformed)

# Cálculo de la importancia media absoluta de cada feature
mean_abs_shap = np.abs(shap_values).mean(axis=0)
importance_df = pd.DataFrame({
    "Feature": X_test_transformed.columns,
    "Mean |SHAP|": mean_abs_shap
}).sort_values("Mean |SHAP|", ascending=False)

# Visualización con Plotly
fig = px.bar(
    importance_df,
    x="Feature",
    y="Mean |SHAP|",
    title="Importancia promedio de las features según SHAP values",
)
fig.show()

In [16]:
shap_values

array([[ 0.11663822, -0.30853838, -0.6050122 , ..., -0.07084622,
        -0.01757217,  0.4623954 ],
       [ 0.21665527,  0.03632927,  0.71760523, ..., -0.04800436,
         0.1743245 ,  0.31931975],
       [ 0.20199266,  0.99170685,  1.1581107 , ..., -0.05014022,
        -0.01090909,  0.3529417 ],
       ...,
       [ 0.3615666 ,  0.14686568,  0.22251047, ..., -0.03143689,
        -0.02321062,  0.3541305 ],
       [-1.3845366 , -0.40690988,  0.17790732, ..., -0.06003824,
        -0.01669055,  0.38217726],
       [-1.0828496 ,  0.07112027,  0.25119755, ..., -0.02625893,
        -0.0157313 , -0.5290131 ]], dtype=float32)

El valor de los Shaps values de forma simple es el aporte de la feature pero a un individuo en especifico, en secciones anteriores estabamos viendo el aporte de las features al modelo en general (aunque para el gráfico se tuvo que hacer una agregación , que seria en este caso el promedio de los Shaps para cada paciente)

Aunque cada lista en shap_values representa a un paciente, los valores dentro de dicha lista es el shap value asociado a una feature (en orden)

La negatividad o positividad indica si la feature aumento la probabilidad de predecir diabetes = 0 o = 1 respectivamente.

### 5.2 Aporte local (4 puntos)

1. Usando los *shap values* calculados, grafique el **aporte local** de las diferentes variables para las instancias **1**, **9** y **150** (1 punto).

2. Interprete sus resultados y responda:

  - ¿Qué variables afectan de manera positiva/negativa a la probabilidad de poseer diabetes? (1 punto)

  - ¿Existe algún patrón común entre las instancias analizadas? (1 punto)

  - ¿Es posible generalizar estas conclusiones a todo el dataset? (1 punto)

In [ ]:
mean_abs_importance = np.abs(shap_values).mean(axis=0)
ordered_features = [f for _, f in sorted(zip(mean_abs_importance, feature_names), reverse=True)]
#Se establecio este orden para mantener fijas las features en el eje y, haciendo mas facil el analisis
# Índices de interés
indices = [1, 9, 150]

# Graficar con orden global fijo
for idx in indices:
    if idx < len(X_test_transformed):
        shap_df = pd.DataFrame({
            "Feature": feature_names,
            "SHAP Value": shap_values[idx],
            "Feature Value": X_test_transformed.iloc[idx].values
        })

        # Mantener orden de las features según importancia media
        shap_df["Feature"] = pd.Categorical(shap_df["Feature"], categories=ordered_features, ordered=True)

        fig = px.bar(
            shap_df.sort_values("Feature"),
            x="SHAP Value",
            y="Feature",
            orientation="h",
            color="SHAP Value",
            color_continuous_scale="RdBu",
            title=f"Aporte local de features - instancia {idx}"
        )
        fig.update_layout(yaxis={'categoryorder': 'array', 'categoryarray': ordered_features})
        fig.show()

Las variables que afectan negativa o positivamente dependen de la persona, pero por ejemplo las personas de instancia 1 y 150, afectan positivamente (clase diabetes = 1) las variables GenHlth, High_BP , pero para la persona 9 es al contrario.

Si bien cambian de signo, las variables GenHlth, Age y HighChlol mantienen un valor absoluto alto de sharp value, indicando que son importantes a la hora de clasificar, hay otras generalidades como por ejemplo que la feature smoker da información importante para catalogar como diabetes = 0.

En cuanto a generalizar estos resultados a todo el dataset, la verdad es que no se podría ya que ya se ve que los resultados no son consistentes entre estos 3 pacientes, generalizar el resultado equivaldria a hacer un experimento con tan solo estas 3 persona, se pierde mucha información.



### 5.3 Aporte global (4 puntos)

Genere ahora una visualización donde se grafique el aporte de cada feature a nivel **global** e interprete sus resultados. ¿Qué diferencias existen con las conclusiones generadas a nivel de instancia?

In [28]:
std_abs = np.abs(shap_values).std(axis=0)
mean_signed = shap_values.mean(axis=0)

df_global = pd.DataFrame({
    "feature": feature_names,
    "mean_abs_shap": mean_abs_importance,
    "std_abs_shap": std_abs,
    "mean_shap": mean_signed
}).sort_values("mean_abs_shap", ascending=False)

# Graficar importancia global (media absoluta) con barras y error (std)
fig = px.bar(
    df_global,
    x="mean_abs_shap",
    y="feature",
    orientation="h",
    error_x="std_abs_shap",
    title="Importancia global de features (media |SHAP|) con desviación estándar",
    labels={"mean_abs_shap": "Media |SHAP|", "feature": "Feature"},
    height=700
)
fig.update_layout(yaxis={"categoryorder":"array","categoryarray":df_global["feature"].tolist()})
fig.show()

# Tabla con top 10 features para referencia
top10 = df_global.head(10).reset_index(drop=True)
top10

feature  mean_abs_shap  std_abs_shap  mean_shap
0               GenHlth       0.626369      0.370018  -0.032921
1                HighBP       0.438031      0.089843  -0.008225
2                   BMI       0.423395      0.288806  -0.011157
3                   Age       0.357401      0.292461  -0.026098
4              HighChol       0.299161      0.077658  -0.023324
5                   Sex       0.097939      0.053262  -0.003121
6  HeartDiseaseorAttack       0.092131      0.099366   0.002020
7              DiffWalk       0.069002      0.047158  -0.001080
8     HvyAlcoholConsump       0.056593      0.133665  -0.000888
9             CholCheck       0.050580      0.187777  -0.009762

Primero se puede ver que sin tomar el valor absoluto la mayoria de las features obtienen un promedio negativo, siendo que a nivel individual los sharp values estaban mas distribuidos en un 50%/50% entre values negativos y positivos, aunque se mantiene la feature de mayor importancia como GenHlth, aunque se puede ver que tambien presenta mayor desviacion estandar.
Tambien la feature CholCheck tiene una gran desviacion estandar comparado con su valor promedio aplicando valor absoluto, y ademas este difere bastante de su valor promedio cuando no se ocupa valor absoluto, esto indicaria que esta feature cambia bastante entre valores positivos y negativos dependiendo del paciente.

### 5.4 Scatter plot (4 puntos)


Grafique ahora un *scatterplot* entre los *shap values* y las primeras 5 features con mayor impacto global (un gráfico por cada feature), coloreando cada punto por la probabilidad de tener diabetes. ¿Qué puede concluir de sus resultados?

In [29]:
# Se calculan las probabilidades de predicción para cada instancia del conjunto de prueba
y_pred_proba = pipe.predict_proba(X_test)[:, 1]

# Se seleccionan las 5 variables con mayor importancia global según el cálculo previo
top_features = df_global.head(5)["feature"].tolist()

# Se crea un DataFrame largo (long format) para facilitar la graficación con Plotly Express
shap_long = pd.DataFrame(shap_values, columns=feature_names)
shap_long["Diabetes_Prob"] = y_pred_proba

# Se filtran solo las features más importantes
shap_long_top = shap_long[top_features + ["Diabetes_Prob"]]

# Se transforma a formato largo
shap_melted = shap_long_top.melt(
    id_vars="Diabetes_Prob",
    value_vars=top_features,
    var_name="Feature",
    value_name="SHAP Value"
)

# Gráfico: un scatter por feature
fig = px.scatter(
    shap_melted,
    x="Feature",
    y="SHAP Value",
    color="Diabetes_Prob",
    color_continuous_scale="RdBu_r",
    title="Relación entre SHAP values y probabilidad de diabetes (Top 5 features)",
    facet_col="Feature",
    facet_col_wrap=2,
    height=700
)
fig.update_layout(showlegend=True)
fig.show()

para GenHlth los shap values son creibles dado que cuando estos son negativos aumenta la probabilidad de ser clase 0, lo mismo sucede con BMI y puede que con HighBP, pero los datos estan muy juntos como para concluir.

Mientras que en Age y HighChol parece que sin importar el valor de shap, se indica más la clase 0 que la clase 1, por lo que los valores de shap difieren de las probabilidades 

### 5.5 Partial Dependence Plot (4 puntos)

Finalmente, se le pide generar un gráfico del tipo Partial Dependence Plot para las mismas 5 variables con mayor impacto global usando una submuestra de 1000 observaciones. ¿Qué relación existe entre la salida promedio del modelo y cada feature analizada? ¿Son estas conclusiones generalizables para todo el conjunto de datos?

In [33]:
sample_idx = X_test.sample(n=min(1000, len(X_test)), random_state=42).index
X_sample = X_test.loc[sample_idx].copy()

n_grid = 50

for feature in top_features:
    col_values = X_sample[feature].dropna()
    low, high = np.quantile(col_values, 0.01), np.quantile(col_values, 0.99)
    grid = np.linspace(low, high, n_grid)

    means = []
    for val in grid:
        X_temp = X_sample.copy()
        X_temp[feature] = val
        probs = pipe.predict_proba(X_temp)[:, 1]
        means.append(probs.mean())

    pdp_df = pd.DataFrame({feature: grid, "PartialDependence": means})

    fig = px.line(
        pdp_df,
        x=feature,
        y="PartialDependence",
        title=f"Partial Dependence Plot - {feature}",
        labels={feature: "Feature value", "PartialDependence": "Salida promedio del modelo"},
        height=400,
        width=800
    )
    fig.update_traces(line=dict(color="steelblue"))
    fig.update_layout(margin=dict(l=60, r=20, t=50, b=60))
    fig.show()

Lo mas evidente de relacion entre feature y la salida promedio son la naturaleza de las variables, por ejemplo las binarias se puede notar una alza al tomar el valor 1, Gen health es escalonada (valores enteros entre 1 y 5) y Age tambien es escalonada aunque menos pronunciada (ya que son valores enteros pero en mayor rango)  finalmente BMI es una continua por lo que el la linea de tendencia varia mucho mas
En general podemos ver que los gráficos son globalmente ascendentes y se puede percibir que BMI y Age tienen zonas donde la probabilidad del modelo clasificar como clase diabetes = 1 disminuye (por ejemplo Age entre 2 y 3 se ve que hay un pequelo bajon comparado con la anterior)

En general en todas estas features se puede decir que entre mayor su valor mas probabilidad hay de predecir clase diabetes = 1

Estos resultados son mas generalizables que en el caso anterior, y considerando que se uso una muestra de 1000 casos elegidos aleatoriamente, se podrían considerar representativos.

## 6. Sistema de Reglas! (10 punto)

<p align="center">
  <img src="https://media.baamboozle.com/uploads/images/125978/1638281150_1380186_gif-url.gif" width="400">
</p>

Después de todo el trabajo hecho, Dr. Simi le pide simplificar el funcionamiento de su modelo en un sistema de reglas que le permita explicar a sus clientes las predicciones que genera su modelo.
En particular, Dr. Simi le pide explicar la decisión tomada para las observaciones **1000**, **3001** y **5751**. Con las reglas propuestas señale a **cuánta población** es posible explicar con estas reglas e indique la **precisión** que poseen las reglas en la totalidad de los datos. ¿Tienen sentido sus reglas propuestas para las observaciones?. Fundamente sus respuesta señalando el impacto que tienen sus reglas sobre todo el conjunto de datos.

`Hint:` Como debe entregar las columnas que entran al clasificador entrenado de su pipeline, le será útil extraer el paso de preprocesamiento y generar dataframes preprocesados para el conjunto `train` y `test`.

In [ ]:
#!pip install alibi

In [22]:
from alibi.explainers import AnchorTabular

In [ ]:
# Función predictora
predict_fn = lambda x: pipe.predict(pd.DataFrame(x, columns=X_test.columns))

# Datos originales y nombres de columnas
X_train_raw = X_train.copy()
feature_names = X_train_raw.columns.tolist()

# Instanciación del explicador con la función predictora
explainer = AnchorTabular(predictor=predict_fn, feature_names=feature_names, seed=0)

# Ajuste del explicador (discretización)
explainer.fit(X_train_raw.values, disc_perc=(25, 50, 75))

# Función para explicar una observación
def explain_index(idx):
    instance = X_test.iloc[idx].values  
    exp = explainer.explain(instance, threshold=0.95)
    print(f"\n=== Explicación Anchor - instancia {idx} ===")
    if hasattr(exp, "anchor"):
        print("Reglas (Anchor):", exp.anchor)
    if hasattr(exp, "precision"):
        print("Precisión de las reglas:", exp.precision)
    if hasattr(exp, "coverage"):
        print("Cobertura de las reglas:", exp.coverage)


for idx in [1000, 3001, 5751]:
    explain_index(idx)


=== Explicación Anchor - instancia 1000 ===
Reglas (Anchor): ['GenHlth > 2.00', 'DiffWalk > 0.00', 'BMI > 25.00', 'Age > 11.00']
Precisión de las reglas: 1.0
Cobertura de las reglas: 0.0379

=== Explicación Anchor - instancia 3001 ===
Reglas (Anchor): ['GenHlth > 2.00', 'HighBP > 0.00', 'Age > 9.00']
Precisión de las reglas: 0.9550359712230215
Cobertura de las reglas: 0.2103

=== Explicación Anchor - instancia 5751 ===
Reglas (Anchor): ['GenHlth > 3.00', 'HeartDiseaseorAttack > 0.00']
Precisión de las reglas: 0.9679144385026738
Cobertura de las reglas: 0.0763


Podemos ver que para la instancia 1000 la precision es perfecta, pero la cobertura solo es para un 4% de la población, po lo que se considera muy especifica, sin embargo las instancias 3001 y 5751, mantienen una precision mayor al 95% y con mayores coberturas, especificamente la instancia 3001 que llega al 21% de la población.

En base a esto podemos ver que no tiene mucho sentido seguir estas reglas de forma global, si no mas bien en agrupaciones locales, por ejemplo la instancia 1000 puede ser asociado a un grupo de personas de mayor edad (maximo despues de la transformacion para edad es 12) y que tienen un BMI relativamente bajo, esto nos da mayor informacion sobre este grupo, pero es un grupo que es pequeño dentro del total de la data, por tanto este proceso ayuda especialmente en conjunto con herramientas como segmentación, pero no de forma generalizada.

# Retrospectiva... (10 puntos)

En base a los diferentes métodos que implementa y ha comentado en este laboratorio, comente qué métodos le permiten entregar mejores conclusiones para la tarea de clasificación de diabetes. Por otro lado, ¿qué métodos son más útiles para el problema del doctor Simi, métodos agnosticos locales o globales?

Por lo visto en el laboratorio creo que los mejores metodos son los que se manejan localmente, dado que le permiten tener un mayor nivel de precision dentro de los datos, creo que valdría la pena considerar metodos de clusterizacion en conjunto con la informacion local para poder clasificar de mejor manera la probabilidad de tener diabetes, una especie de "probabilidad de tener diabetes condicionado a ser del grupo X", aunque siempre esta bien considerar los resultados globales, aunque no se implementen directamente, por ejemplo se vio en la parte 5.3 que features como CholCheck diferian mucho de shap value entre pacientes, es bueno tener esto en cuenta al revisar los resultados de esa feature en la clusterizacion por ejemplo.

Cabe recalcar que tambien hay que considerar el aumento de complejidad del problema cuando se decide tratar localmente en vez de globalizar, en este caso se cree relevante puesto que hay heterogeneidad entre bastante de las features, ademas que los problemas de salud (mas aun los de alto impaco social como el cancer, diabetes, etc) suele ser mucho mas importante asegurar un buen rendimiento de modelo (sobre todo en metricas como recall), pero en un modelo con datos mas homogeneos o donde el costo de fallas predicciones no sea tan alto, podría ser preferible usar reglas generalizables al mayor porcentaje de la población.

<a style='text-decoration:none;line-height:16px;display:flex;color:#5B5B62;padding:10px;justify-content:end;' href='https://deepnote.com?utm_source=created-in-deepnote-cell&projectId=87110296-876e-426f-b91d-aaf681223468' target="_blank">
 </img>
Created in <span style='font-weight:600;margin-left:4px;'>Deepnote</span></a>